In [1]:
import numpy as np
import scipy.stats
from scipy.stats import spearmanr
import scipy.spatial
from sklearn.model_selection import KFold
import random
from sklearn.metrics import mean_squared_error
from math import sqrt
import math
import warnings
import sys
import time
users = 1683
items = 1683
start=time.time();
#extract the data from file to matrix
f = open('u.data',"r")
data = []
for row in f:
    r = row.split('\t')
    e = [int(r[0]), int(r[1]), int(r[2])]
    data.append(e)
#print(data)
k_fold = KFold(n_splits=4) #to split and make a training set data 4 folds
#print(k_fold.get_n_splits(data))
#print (k_fold.split(data))
Mat = np.zeros((users,items))
for e in data:
    Mat[e[0]-1][e[1]-1] = e[2]
    #print( Mat[e[0]-1][e[1]-1] )
item_similarity_pearson = np.zeros((items,items))
#print([item[0] for item in data])
#print (Mat[:][0])
print('start')
## find the similarity between two items using pearson coefficient
for item1 in range(items):
    #print (type(data))
    for item2 in range(items):
        #R = [item[item1] for item in data]
        #print('here', item1)
        #Q = np.array(data)[:,item2]
        if np.count_nonzero(Mat[:][item1]) and np.count_nonzero(Mat[:][item2]):
            #print('here')
            try:
                pearson_result = scipy.stats.pearsonr(Mat[:][item1],Mat[:][item2])
                #print(pearson_result,math.isnan(pearson_result[0]))
                if not math.isnan(pearson_result[0]):
                    item_similarity_pearson[item1][item2] = pearson_result[0]
                    #print(item_similarity_pearson[item1][item2])
                else:
                    item_similarity_pearson[item1][item2] = 0
            except:
                item_similarity_pearson[item1][item2] = 0
#print(item_similarity_pearson)
print('done')


start
done


In [2]:
##prediction
sim_item_pearson = item_similarity_pearson
#print(sim_item_pearson[9])
rmse = []
rmse_pearson = []
prec_on_top_k = []
spearman_pearson = []
precicion =0
for train_indices, test_indices in k_fold.split(data):
    match_prec = 0
    count_prec =0
    train = [data[i] for i in train_indices] #training data
    test = [data[i] for i in test_indices] #testing data 
    M = np.zeros((users,items))
    for e in train:
        M[e[0]-1][e[1]-1] = e[2]
    true_rate = []
    pred_rate_pearson = []
    for e in test:
            user = e[0]
            item = e[1]
            true_rate.append(e[2])
            pred_pearson = 3.0
            #print(np.count_nonzero(M[:][item-1]))
            if np.count_nonzero(M[:][item-1]):
                #print('here')
                sim_pearson = sim_item_pearson[:][item-1]
                ind = (M[user-1][:] > 0)
                #print(ind)
                #ind[item-1] = False
                #print (sim_pearson[ind])
                ind2 = np.argpartition(sim_pearson, -10)[-10:]
                print(np.count_nonzero(sim_pearson))
                print(ind2)
                #print('items ', items)
                for z in range(items):
                    #print(z)
                    if z not in ind2:
                        #print('in')
                        sim_pearson[int(z)] = 0  
                #print(np.count_nonzero(sim_pearson))
                normal_pearson = np.sum(np.absolute(sim_pearson[ind]))
                if normal_pearson > 0:
                    pred_pearson = np.dot(sim_pearson,M[user-1][:])/normal_pearson ##calculating the pearson coeff
            if pred_pearson < 0:
                pred_pearson = 0
            if pred_pearson > 5:
                pred_pearson = 5
            print (str(user),"\t",str(item),"\t",str(e[2]),"\t", str(pred_pearson))
            pred_rate_pearson.append(pred_pearson)
            ##for precision
            count_prec = count_prec+1
            if (pred_pearson == e[2]):
                match_prec = match_prec +1
    precision = float((match_prec*100))/count_prec
    prec_on_top_k.append(precision)
    
##calculate the errors
    spcoef, p = spearmanr(true_rate, pred_rate_pearson) ##spearman test for evaluation
    spearman_pearson.append(spcoef)
    rmse_pearson.append(sqrt(mean_squared_error(true_rate, pred_rate_pearson)))  ##root mean square
            #print (str(sqrt(mean_squared_error(true_rate, pred_rate_pearson))))
\print("%s seconds" %(time.time()-start)) ##print the time taken. #2532.67 seconds
#print(rmse_pearson)
print(np.mean(rmse_pearson)) #1.748647526728496
print(np.mean(prec_on_top_k))  #75.625364
#print(spearman_pearson)
print(np.mean(spearman_pearson))  #0.999999999999934







943
[707 516 768 856  92 251 241 836   1 180]
196 	 242 	 3 	 3.0
943
[724 852 430 528 442 334 800 501 749 301]
186 	 302 	 3 	 3.0
943
[588 813 728 501 254 939 625 133 376 407]
22 	 377 	 1 	 3.0
943
[830 487 699 678 747 745 349 697  50 631]
244 	 51 	 2 	 3.0
943
[745 300 670 550 266 346 681 108 652 345]
166 	 346 	 1 	 5.0
943
[845 193  17 665  58 715 536 270 473 233]
298 	 474 	 4 	 3.0
943
[688 551 713 431 140 758 264 705 702 729]
115 	 265 	 2 	 3.0
943
[  5 697 746  81 912 747 236 464 866 837]
253 	 465 	 5 	 2.9999999999999996
943
[509 749 852  34 586 723 450 488 528 172]
305 	 451 	 3 	 3.0
943
[172 897 308 754 407 204 749 128 739  85]
6 	 86 	 3 	 3.6625370452151693
943
[793 827  62  67 459 265 256 893 448 883]
62 	 257 	 2 	 3.0
286 	 1014 	 5 	 3.0
943
[486  55 863  91 275 756 550 681 221 108]
200 	 222 	 5 	 3.0
943
[862 272 427 148 914 573  39 447 672 283]
210 	 40 	 3 	 3.0
943
[686 445 361 148 432 172 219  28 826 430]
224 	 29 	 3 	 2.0
943
[653 699 907  15 537 738 866 

943
[ 63   6 773 649 325 378 270 737 193 312]
286 	 379 	 5 	 3.0
943
[842 737 715 748 891 312 617 814 649 289]
244 	 815 	 4 	 2.9999999999999996
943
[660 898 895 737 487 747 456 197 624 478]
7 	 479 	 4 	 3.3341327810112995
943
[117 801 603 813 545  20  27 365 366 367]
174 	 368 	 1 	 2.9999999999999996
10
[180 713 592 937 264 402 702 167 273 707]
87 	 274 	 4 	 5.0
194 	 1211 	 2 	 3.0
82 	 1134 	 2 	 3.0
943
[104  47 874 780 213 703 835 555 709 314]
13 	 836 	 2 	 3.0
943
[644 390 889 537 297 685 526 932 928 271]
13 	 272 	 4 	 5.0
943
[483 377 843 881 884 289 755  69 108 737]
244 	 756 	 2 	 4.0
10
[852 488 754 445 308 172 139 426 450 586]
305 	 427 	 5 	 3.0
943
[283 403 826 783 862 786 723 754 872 914]
95 	 787 	 2 	 3.0
943
[536 473 746 912  57 526 263 343  13  17]
43 	 14 	 2 	 3.4946672725893144
299 	 955 	 4 	 3.0
943
[464 502  24 337  70 837 703 375 418 359]
57 	 419 	 3 	 3.0
943
[ 58 221  93 617 378 193 711 404 845 310]
84 	 405 	 3 	 3.0
943
[209 406 312 748 456 449 880 

83 	 623 	 4 	 3.0
943
[268 497 338 591 333 342 536 473 298 757]
214 	 334 	 3 	 3.0
10
[541  86  21 282 689 263 578 475 335 124]
192 	 476 	 2 	 3.0
943
[473 333 853  61 296 653 344 343 513  42]
100 	 344 	 4 	 3.0
943
[434 373 275 221 550 547  91 331 144 129]
268 	 145 	 1 	 4.0
943
[393 647 221 544 483 300 496 863 108  55]
301 	 56 	 4 	 5.0
943
[462 568 769 677 364 360 729 581 767  88]
307 	 89 	 5 	 3.0
943
[458  25 163 264 395 824 937 167 551 140]
234 	 141 	 3 	 2.481224194892352
943
[741 469 401  65 705 702 729 437 107 575]
83 	 576 	 4 	 3.0
10
[406 378 326  13 360 475 217 263 314 578]
181 	 264 	 2 	 3.0156899940726722
943
[615 132 862 855 925 817 111 352  99 204]
297 	 133 	 4 	 5.0
943
[465 176  90 487   7 709 196 162 574 152]
38 	 153 	 5 	 3.0
10
[874  72 268 122  70   5 390 526 113 381]
7 	 382 	 4 	 3.999916947130849
943
[514 783 588 257 488 427 280 501 812 301]
264 	 813 	 4 	 3.0
943
[347 100 180 767 264 629 140 871 189 717]
181 	 872 	 1 	 1.0
943
[283 573 919 170 77

234 	 612 	 3 	 3.0
10
[ 31 520  98 431 346 116 492 688 250  56]
104 	 117 	 2 	 3.0
943
[428 406 362 296 333 757 292 591 302 275]
38 	 758 	 1 	 3.0
943
[719 573 786 610 844 148 283 128 205 170]
269 	 845 	 1 	 3.0
943
[152 855 352 383 178 615 826 287 162 355]
7 	 163 	 4 	 4.016575488164171
234 	 1451 	 3 	 3.0
10
[ 58 193 310 221 378 617 711 845 404  93]
275 	 405 	 2 	 3.0
943
[912 617 275 737 605 591 296 176 918 249]
52 	 250 	 3 	 5.0
943
[ 15 885 513 895 863 932 915 822 193  63]
102 	 823 	 3 	 3.0
943
[129 618 327 373 632 346 331 185 547 255]
13 	 186 	 4 	 3.4981215889684005
943
[693 453 233 270 297 715 911 127 397 730]
178 	 731 	 4 	 2.0
943
[418 369 408  40 381 873 295 231  70  72]
236 	 71 	 3 	 3.0
943
[214 889 537 780 709  90 928 932 176 685]
256 	 781 	 5 	 5.0
943
[ 53 175 103  31 149 769 466 623 581 469]
263 	 176 	 5 	 3.0
10
[129 618 327 547 255 346 632 373 185 331]
244 	 186 	 3 	 3.0
279 	 1181 	 4 	 3.0
10
[842 748 715 891 617 649 814 737 289 312]
43 	 815 	 4 	 

21 	 370 	 1 	 3.0
943
[591 605 275 176 888 714 296 912 520 248]
293 	 249 	 3 	 3.4966916350527537
943
[487 532 426 177 223 513 628 172 450 720]
264 	 721 	 5 	 5.0
943
[110 427 228 712 170 751 914 862 610 283]
10 	 611 	 5 	 3.0
10
[745 300 670 266 652 681 346 345 550 108]
197 	 346 	 3 	 3.0
943
[465 417 940 874 800 864 591 141 267 821]
276 	 142 	 3 	 3.0
10
[852 488 754 445 308 172 139 426 450 586]
308 	 427 	 4 	 5.0
943
[215 681 585 708 300 631 550 932 221 942]
221 	 943 	 4 	 3.0
943
[352 488 586 771 125  99 817 925 257 808]
131 	 126 	 4 	 3.0
943
[586 528 686 450 154 363 823 139 509 169]
268 	 824 	 2 	 3.0
943
[157  36 745 351 465 599 196 618   7 825]
109 	 8 	 3 	 3.0
943
[591 467  63 304 326 296 536 513 213  57]
198 	 58 	 3 	 4.0
943
[568 198  25 276  16 679 729 793 657 130]
230 	 680 	 4 	 3.0
943
[214 124 863 795 177 532  41 740 617 898]
181 	 741 	 1 	 2.0
192 	 1061 	 4 	 3.0
943
[ 39 106  46 447 146 148 573 719 170 283]
234 	 448 	 3 	 2.0
943
[ 73 909 905 613 928 90

...

895 	 1 	 4 	 3.0
10
[403 749 786 280 430 754 723 852 172 399]
790 	 755 	 3 	 3.0
10
[ 67 702 549 707 799 713 516 758 894 688]
716 	 517 	 5 	 3.0
10
[383 543 771 355 104 855 625 407  38 897]
634 	 408 	 3 	 3.0
543 	 947 	 4 	 3.0
10
[631 617 863 310 576 289 881  41 483 896]
521 	 42 	 5 	 3.0
10
[110 610 862 914 283 774 170 573 783 111]
916 	 284 	 2 	 3.0
10
[289  69 544 745 483 704 756  82 216  55]
892 	 705 	 4 	 3.0
10
[399 862 528 826 588  32 723 800 501 811]
864 	 801 	 3 	 3.0
10
[ 42 456 587 302 406 416 513 750 285 659]
382 	 286 	 2 	 3.0
10
[936 198 525 838   1 208  62 485 130 734]
889 	 209 	 2 	 3.0
10
[106 281 172 569  46 925 219 283 170 447]
749 	 47 	 4 	 3.5491181864295482
10
[362  93 550 221 434 302 275 681 300  91]
938 	 276 	 3 	 3.0
10
[289  69 544 745 483 704 756  82 216  55]
488 	 705 	 4 	 3.507359560612993
10
[450 862 919 852 840 728 142 355 509 259]
832 	 260 	 3 	 3.0
59 	 1114 	 5 	 3.0
10
[673 937 100 778 713 549 688 758 878 702]
279 	 779 	 3 	 3.5041120

10
[400 397  84 206 715 209 193 473 270 317]
524 	 318 	 4 	 3.4840953827150996
10
[533 167 824 402 551 180 707 517 100 356]
788 	 357 	 4 	 2.6748879092755824
10
[497 526 176 912 114 247 537  95 420 351]
883 	 421 	 5 	 3.0
883 	 952 	 3 	 3.0
429 	 1018 	 3 	 3.0
804 	 1060 	 3 	 3.0
10
[747 513 372  63 737 428 822 863 456 342]
747 	 514 	 4 	 3.0
10
[190 686 484 128 228 615 239 826 925 739]
542 	 240 	 3 	 5.0
10
[265 594 175 788 472  49 226 469  26 149]
749 	 50 	 5 	 4.0
10
[487  63 652 842  43 889 932 737 649 214]
916 	 215 	 3 	 3.0
110 	 947 	 3 	 3.0
10
[100  56 653 313 458 871 167 140 629 222]
165 	 223 	 4 	 3.0
10
[649 483 814 544 274 253  41 737 880 289]
852 	 290 	 4 	 3.0
10
[ 32 257 855 509 142 399 165 815  60 514]
894 	 166 	 4 	 4.0
10
[172 543 852 754 399 430 528 569 450 749]
894 	 750 	 4 	 3.0
10
[100 402 167 878 677 673 524 713 707 799]
902 	 879 	 4 	 3.0
10
[688 551 431 702 758 264 729 140 713 705]
270 	 265 	 4 	 4.0
10
[ 84 473 193 663  17 747 822 292 839 150]

10
[799 633 119  65 636 673  67 705 548 934]
847 	 120 	 1 	 3.0
10
[334 723 751 586 316 615 862 783   2 488]
880 	 3 	 1 	 3.0
10
[ 58 193 310 221 378 617 711 845 404  93]
518 	 405 	 5 	 5.0
10
[347 180 100 629 717 767 264 140 189 871]
655 	 872 	 3 	 3.0
712 	 1480 	 4 	 3.0
10
[ 53  31 623 769 466 469 149 103 175 581]
25 	 176 	 4 	 3.0
10
[456 377  64  93 532  58 513 270 296  10]
886 	 11 	 5 	 3.0
10
[149 276 466 623 539 156  25  53 633 103]
890 	 157 	 4 	 3.0
10
[504 617 537 327 300 932 187 456 692 631]
694 	 188 	 5 	 4.0
10
[450 802 588 399 790 257 754 139 739 731]
881 	 732 	 5 	 4.0
10
[748 406  43 647 726 649 737 803 393 659]
496 	 660 	 3 	 5.0
10
[771 128 833 132 790 700 808 412 443 817]
749 	 444 	 2 	 4.0
10
[431  44  56 713 246 729 702 688  52 212]
388 	 53 	 5 	 3.0
10
[814 397 229 297 289 884 540 881 339 785]
704 	 340 	 3 	 3.0
10
[723 862 514 178 352 417 586 919 819 205]
781 	 179 	 5 	 3.0
10
[418 369 408  70 381  72 231  40 295 873]
682 	 71 	 5 	 3.000000000000

401 	 405 	 2 	 4.0
10
[605 456 867 617 478 652  63 737 197 932]
10 	 198 	 3 	 4.478440978075527
10
[783 409 855 645 509 811 355 588 257 630]
689 	 258 	 5 	 1.0
10
[ 64 313  42 587 377 415 173 151 344 592]
5 	 174 	 5 	 1.0
891 	 978 	 4 	 3.0
10
[815 819 723 808 855 771 355 142 528 840]
921 	 143 	 5 	 3.0
10
[732 149 469 472 935 788 226 633 500 589]
23 	 227 	 3 	 3.0
10
[912 513 275 302 942 885 452 863 215 631]
848 	 216 	 5 	 3.0
10
[265 594 175 788 472  49 226 469  26 149]
739 	 50 	 4 	 1.0
10
[826 442 508 586  46 219 104 281 106 569]
869 	 282 	 3 	 3.0
10
[809 831 169 852 204 257 450 509 815 811]
747 	 510 	 5 	 5.0
10
[400 397  84 206 715 209 193 473 270 317]
913 	 318 	 4 	 2.0
10
[795 641 372  55 415 377 617 587 863  42]
835 	 588 	 3 	 3.0
10
[122 358   8 679 739 595 729 796 734 432]
723 	 9 	 3 	 3.0
10
[ 46 228 139 363 739 104 731 106 684 281]
935 	 685 	 4 	 3.0
10
[802 674 672 447 228 573 655 110 148 865]
537 	 675 	 3 	 2.9999999999999996
10
[289  69 544 745 483 704 

943 	 391 	 2 	 3.0
10
[ 46 228 139 363 739 104 731 106 684 281]
864 	 685 	 4 	 3.995948715747294
10
[788 591 220 346 431 833 322  98 176  68]
750 	 323 	 3 	 3.0
10
[891 513 487 822 631 737 197 895  63 932]
279 	 64 	 1 	 3.4882807803217184
10
[172 543 852 754 399 430 528 569 450 749]
646 	 750 	 3 	 3.0
10
[ 76 663 839 408  47 473 703 665 552 369]
654 	 370 	 2 	 3.0
10
[431 702  31 175 623 729 581 688 769  25]
617 	 582 	 4 	 3.0
10
[378  55 300  91 863 221 193  86 689 370]
913 	 690 	 3 	 2.494740197819644
10
[148 655 110 409 925 228 610 239 712 672]
660 	 229 	 2 	 2.0
10
[ 63 832 536 338 497   5 663 566 268 333]
421 	 498 	 4 	 3.0
495 	 1091 	 4 	 3.0
10
[497 526 176 912 114 247 537  95 420 351]
806 	 421 	 4 	 2.9999999999999996
10
[912 351  63 537 747 737 932 785 631 822]
676 	 538 	 4 	 3.3580307760396524
10
[229 456 415 592 377 261 617 329  42 884]
721 	 262 	 3 	 3.0000000000000004
10
[936 198 525 838   1 208  62 485 130 734]
913 	 209 	 2 	 3.0
10
[139 767 524 562 191 219